In [1]:
import pandas as pd
import numpy as np
import os
import time
import collections

#import matplot.lib

import gensim
from gensim.models.doc2vec import Doc2Vec, TaggedDocument
assert gensim.models.doc2vec.FAST_VERSION > -1 #parallelize doc2vec
from gensim.utils import simple_preprocess

In [2]:
import multiprocessing

workers = multiprocessing.cpu_count()

In [3]:
import logging
logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)

In [4]:
#os.chdir('Patent Claims')

os.chdir('D:\Datasets')

In [5]:
%%time
df=pd.read_csv('claim_2000_2014_cleaned.csv',usecols=['claim_no','claim_txt','ICL','ICC','litigation'])


Wall time: 1min 15s


In [6]:
df.head()

claim_no                                          claim_txt  ICL  ICC  \
0  8697278-17  battery comprising interior battery active ele...  106    2   
1   8697278-1  battery cell casing comprising first casing el...   97    2   
2  7385756-81  catadioptric projection objective imaging patt...  108   33   
3  7385756-94  catadioptric projection objective imaging patt...  116   33   
4  7385756-79  catadioptric projection objective imaging patt...  103   33   

   litigation  
0           0  
1           0  
2           0  
3           0  
4           0

In [7]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 8216031 entries, 0 to 8216030
Data columns (total 5 columns):
claim_no      object
claim_txt     object
ICL           int64
ICC           int64
litigation    int64
dtypes: int64(3), object(2)
memory usage: 313.4+ MB


In [6]:
#MAIN MODEL 'Doc2vec_Patent_Claims_FINAL_dm_30e'
# Is Trained using every independent claim with lexNLP stopwords removed and Tagged by 
# patent#-claim# as the paragraph id


#Experimental mode1l
# Is Trained using every independent claim with lexNLP stopwords removed  
# Tagged by '0 or 1 for litigation classification#' as the paragraph id
class MyDataframeCorpus(object):
    def __init__(self, source_df, text_col, tag_col):
        self.source_df = source_df
        self.text_col = text_col
        self.tag_col = tag_col
      
    def __iter__(self):
        for i, row in self.source_df.iterrows():
            yield TaggedDocument(words=simple_preprocess(row[self.text_col]), 
                                 tags=[row[self.tag_col]])
###MAIN MODEL
corpus_for_doc2vec = MyDataframeCorpus(df, 'claim_txt', 'claim_no')
###EXPERIMENTAL MODEL
#corpus_for_doc2vec = MyDataframeCorpus(df, 'claim_txt', 'litigation')

In [13]:
#corpus_for_doc2vec = MyDataframeCorpus(df, 'claim_txt', 'claim_no')

In [14]:

#Params
model_smple = Doc2Vec(vector_size=100, # 100 should be fine based on the standards
                window=8, #change to 8
                alpha=.025, #initial learning rate
                min_alpha=0.00025, #learning rate drops linearly to this
                min_count=2, #ignores all words with total frequency lower than this.
                dm =1, #algorith 1=distributed memory , 0=distributed bag of words (PV-DBOW)
                epochs=30,
                workers=workers)#cores to use

In [15]:
%%time
model_smple.build_vocab(corpus_for_doc2vec,progress_per=500000)

## Build vocab from streaming tagged document Show progress every 500k rows
## Should take ~ 30 minutes

2019-07-17 11:47:47,765 : INFO : collecting all words and their counts
2019-07-17 11:47:48,963 : INFO : PROGRESS: at example #0, processed 0 words (0/s), 0 word types, 0 tags
2019-07-17 11:49:39,085 : INFO : PROGRESS: at example #500000, processed 49597140 words (450386/s), 86304 word types, 2 tags
2019-07-17 11:51:30,891 : INFO : PROGRESS: at example #1000000, processed 100266438 words (453332/s), 122900 word types, 2 tags
2019-07-17 11:53:24,396 : INFO : PROGRESS: at example #1500000, processed 151452388 words (450958/s), 151795 word types, 2 tags
2019-07-17 11:55:17,007 : INFO : PROGRESS: at example #2000000, processed 202518153 words (453472/s), 176503 word types, 2 tags
2019-07-17 11:57:10,641 : INFO : PROGRESS: at example #2500000, processed 254066538 words (453639/s), 199076 word types, 2 tags
2019-07-17 11:59:04,881 : INFO : PROGRESS: at example #3000000, processed 306104677 words (455520/s), 221238 word types, 2 tags
2019-07-17 12:00:59,044 : INFO : PROGRESS: at example #35000

Wall time: 31min 35s


In [16]:
%%time
model_smple.train(corpus_for_doc2vec, total_examples=model_smple.corpus_count, epochs=model_smple.epochs)
#train the model

2019-07-17 13:24:38,072 : INFO : training model with 16 workers on 282370 vocabulary and 100 features, using sg=0 hs=0 sample=0.001 negative=5 window=8
2019-07-17 13:24:46,859 : INFO : EPOCH 1 - PROGRESS: at 0.00% examples, 987 words/s, in_qsize 31, out_qsize 0
2019-07-17 13:24:47,873 : INFO : EPOCH 1 - PROGRESS: at 0.04% examples, 32604 words/s, in_qsize 31, out_qsize 0
2019-07-17 13:24:48,874 : INFO : EPOCH 1 - PROGRESS: at 0.08% examples, 57242 words/s, in_qsize 32, out_qsize 0
2019-07-17 13:24:49,910 : INFO : EPOCH 1 - PROGRESS: at 0.12% examples, 78582 words/s, in_qsize 32, out_qsize 0
2019-07-17 13:24:50,921 : INFO : EPOCH 1 - PROGRESS: at 0.17% examples, 95687 words/s, in_qsize 31, out_qsize 0
2019-07-17 13:24:51,934 : INFO : EPOCH 1 - PROGRESS: at 0.21% examples, 109810 words/s, in_qsize 31, out_qsize 0
2019-07-17 13:24:52,946 : INFO : EPOCH 1 - PROGRESS: at 0.26% examples, 123570 words/s, in_qsize 31, out_qsize 0
2019-07-17 13:24:53,961 : INFO : EPOCH 1 - PROGRESS: at 0.30% ex

2019-07-17 13:26:00,164 : INFO : EPOCH 1 - PROGRESS: at 3.06% examples, 269384 words/s, in_qsize 31, out_qsize 0
2019-07-17 13:26:01,182 : INFO : EPOCH 1 - PROGRESS: at 3.10% examples, 269695 words/s, in_qsize 31, out_qsize 0
2019-07-17 13:26:02,193 : INFO : EPOCH 1 - PROGRESS: at 3.14% examples, 270029 words/s, in_qsize 32, out_qsize 0
2019-07-17 13:26:03,204 : INFO : EPOCH 1 - PROGRESS: at 3.18% examples, 270271 words/s, in_qsize 31, out_qsize 0
2019-07-17 13:26:04,223 : INFO : EPOCH 1 - PROGRESS: at 3.22% examples, 270579 words/s, in_qsize 31, out_qsize 0
2019-07-17 13:26:05,244 : INFO : EPOCH 1 - PROGRESS: at 3.26% examples, 270885 words/s, in_qsize 31, out_qsize 0
2019-07-17 13:26:06,289 : INFO : EPOCH 1 - PROGRESS: at 3.30% examples, 271105 words/s, in_qsize 32, out_qsize 0
2019-07-17 13:26:07,312 : INFO : EPOCH 1 - PROGRESS: at 3.35% examples, 271364 words/s, in_qsize 32, out_qsize 0
2019-07-17 13:26:08,332 : INFO : EPOCH 1 - PROGRESS: at 3.39% examples, 271538 words/s, in_qsize

2019-07-17 13:27:14,328 : INFO : EPOCH 1 - PROGRESS: at 6.11% examples, 284585 words/s, in_qsize 31, out_qsize 0
2019-07-17 13:27:15,351 : INFO : EPOCH 1 - PROGRESS: at 6.14% examples, 284712 words/s, in_qsize 31, out_qsize 0
2019-07-17 13:27:16,372 : INFO : EPOCH 1 - PROGRESS: at 6.19% examples, 284846 words/s, in_qsize 31, out_qsize 0
2019-07-17 13:27:17,393 : INFO : EPOCH 1 - PROGRESS: at 6.23% examples, 284965 words/s, in_qsize 31, out_qsize 0
2019-07-17 13:27:18,402 : INFO : EPOCH 1 - PROGRESS: at 6.27% examples, 285171 words/s, in_qsize 31, out_qsize 0
2019-07-17 13:27:19,407 : INFO : EPOCH 1 - PROGRESS: at 6.31% examples, 285245 words/s, in_qsize 31, out_qsize 0
2019-07-17 13:27:20,408 : INFO : EPOCH 1 - PROGRESS: at 6.35% examples, 285354 words/s, in_qsize 32, out_qsize 0
2019-07-17 13:27:21,426 : INFO : EPOCH 1 - PROGRESS: at 6.39% examples, 285465 words/s, in_qsize 31, out_qsize 0
2019-07-17 13:27:22,435 : INFO : EPOCH 1 - PROGRESS: at 6.44% examples, 285599 words/s, in_qsize

2019-07-17 13:28:28,384 : INFO : EPOCH 1 - PROGRESS: at 9.14% examples, 291054 words/s, in_qsize 31, out_qsize 0
2019-07-17 13:28:29,389 : INFO : EPOCH 1 - PROGRESS: at 9.18% examples, 291056 words/s, in_qsize 31, out_qsize 0
2019-07-17 13:28:30,403 : INFO : EPOCH 1 - PROGRESS: at 9.23% examples, 291079 words/s, in_qsize 31, out_qsize 0
2019-07-17 13:28:31,410 : INFO : EPOCH 1 - PROGRESS: at 9.26% examples, 291112 words/s, in_qsize 31, out_qsize 0
2019-07-17 13:28:32,449 : INFO : EPOCH 1 - PROGRESS: at 9.30% examples, 291151 words/s, in_qsize 32, out_qsize 0
2019-07-17 13:28:33,468 : INFO : EPOCH 1 - PROGRESS: at 9.35% examples, 291207 words/s, in_qsize 32, out_qsize 0
2019-07-17 13:28:34,490 : INFO : EPOCH 1 - PROGRESS: at 9.39% examples, 291298 words/s, in_qsize 31, out_qsize 0
2019-07-17 13:28:35,512 : INFO : EPOCH 1 - PROGRESS: at 9.43% examples, 291276 words/s, in_qsize 32, out_qsize 0
2019-07-17 13:28:36,520 : INFO : EPOCH 1 - PROGRESS: at 9.47% examples, 291347 words/s, in_qsize

2019-07-17 13:29:42,496 : INFO : EPOCH 1 - PROGRESS: at 12.16% examples, 293920 words/s, in_qsize 31, out_qsize 0
2019-07-17 13:29:43,511 : INFO : EPOCH 1 - PROGRESS: at 12.20% examples, 293967 words/s, in_qsize 31, out_qsize 0
2019-07-17 13:29:44,516 : INFO : EPOCH 1 - PROGRESS: at 12.24% examples, 294019 words/s, in_qsize 31, out_qsize 0
2019-07-17 13:29:45,523 : INFO : EPOCH 1 - PROGRESS: at 12.28% examples, 294038 words/s, in_qsize 31, out_qsize 0
2019-07-17 13:29:46,567 : INFO : EPOCH 1 - PROGRESS: at 12.32% examples, 294044 words/s, in_qsize 31, out_qsize 0
2019-07-17 13:29:47,573 : INFO : EPOCH 1 - PROGRESS: at 12.37% examples, 294061 words/s, in_qsize 31, out_qsize 0
2019-07-17 13:29:48,591 : INFO : EPOCH 1 - PROGRESS: at 12.41% examples, 294101 words/s, in_qsize 31, out_qsize 0
2019-07-17 13:29:49,595 : INFO : EPOCH 1 - PROGRESS: at 12.45% examples, 294124 words/s, in_qsize 31, out_qsize 0
2019-07-17 13:29:50,616 : INFO : EPOCH 1 - PROGRESS: at 12.49% examples, 294187 words/s,

...

2019-07-18 10:53:00,096 : INFO : EPOCH 30 - PROGRESS: at 90.59% examples, 304173 words/s, in_qsize 31, out_qsize 0
2019-07-18 10:53:01,102 : INFO : EPOCH 30 - PROGRESS: at 90.63% examples, 304176 words/s, in_qsize 31, out_qsize 0
2019-07-18 10:53:02,125 : INFO : EPOCH 30 - PROGRESS: at 90.67% examples, 304180 words/s, in_qsize 31, out_qsize 0
2019-07-18 10:53:03,140 : INFO : EPOCH 30 - PROGRESS: at 90.71% examples, 304185 words/s, in_qsize 31, out_qsize 0
2019-07-18 10:53:04,149 : INFO : EPOCH 30 - PROGRESS: at 90.75% examples, 304187 words/s, in_qsize 31, out_qsize 0
2019-07-18 10:53:05,173 : INFO : EPOCH 30 - PROGRESS: at 90.79% examples, 304187 words/s, in_qsize 31, out_qsize 0
2019-07-18 10:53:06,188 : INFO : EPOCH 30 - PROGRESS: at 90.83% examples, 304189 words/s, in_qsize 31, out_qsize 0
2019-07-18 10:53:07,196 : INFO : EPOCH 30 - PROGRESS: at 90.87% examples, 304195 words/s, in_qsize 31, out_qsize 0
2019-07-18 10:53:08,198 : INFO : EPOCH 30 - PROGRESS: at 90.91% examples, 304197

2019-07-18 10:54:13,076 : INFO : EPOCH 30 - PROGRESS: at 93.44% examples, 304385 words/s, in_qsize 31, out_qsize 0
2019-07-18 10:54:14,076 : INFO : EPOCH 30 - PROGRESS: at 93.48% examples, 304388 words/s, in_qsize 31, out_qsize 0
2019-07-18 10:54:15,109 : INFO : EPOCH 30 - PROGRESS: at 93.52% examples, 304391 words/s, in_qsize 32, out_qsize 0
2019-07-18 10:54:16,127 : INFO : EPOCH 30 - PROGRESS: at 93.56% examples, 304391 words/s, in_qsize 31, out_qsize 0
2019-07-18 10:54:17,148 : INFO : EPOCH 30 - PROGRESS: at 93.60% examples, 304391 words/s, in_qsize 31, out_qsize 0
2019-07-18 10:54:18,155 : INFO : EPOCH 30 - PROGRESS: at 93.64% examples, 304394 words/s, in_qsize 31, out_qsize 0
2019-07-18 10:54:19,171 : INFO : EPOCH 30 - PROGRESS: at 93.68% examples, 304395 words/s, in_qsize 32, out_qsize 0
2019-07-18 10:54:20,209 : INFO : EPOCH 30 - PROGRESS: at 93.72% examples, 304397 words/s, in_qsize 32, out_qsize 0
2019-07-18 10:54:21,217 : INFO : EPOCH 30 - PROGRESS: at 93.76% examples, 304403

2019-07-18 10:55:26,311 : INFO : EPOCH 30 - PROGRESS: at 96.28% examples, 304595 words/s, in_qsize 31, out_qsize 0
2019-07-18 10:55:27,330 : INFO : EPOCH 30 - PROGRESS: at 96.32% examples, 304596 words/s, in_qsize 31, out_qsize 0
2019-07-18 10:55:28,341 : INFO : EPOCH 30 - PROGRESS: at 96.36% examples, 304601 words/s, in_qsize 32, out_qsize 0
2019-07-18 10:55:29,356 : INFO : EPOCH 30 - PROGRESS: at 96.40% examples, 304606 words/s, in_qsize 32, out_qsize 0
2019-07-18 10:55:30,401 : INFO : EPOCH 30 - PROGRESS: at 96.44% examples, 304607 words/s, in_qsize 31, out_qsize 0
2019-07-18 10:55:31,404 : INFO : EPOCH 30 - PROGRESS: at 96.48% examples, 304610 words/s, in_qsize 31, out_qsize 0
2019-07-18 10:55:32,415 : INFO : EPOCH 30 - PROGRESS: at 96.52% examples, 304616 words/s, in_qsize 32, out_qsize 0
2019-07-18 10:55:33,436 : INFO : EPOCH 30 - PROGRESS: at 96.56% examples, 304616 words/s, in_qsize 32, out_qsize 0
2019-07-18 10:55:34,465 : INFO : EPOCH 30 - PROGRESS: at 96.60% examples, 304619

2019-07-18 10:56:39,494 : INFO : EPOCH 30 - PROGRESS: at 99.09% examples, 304798 words/s, in_qsize 31, out_qsize 0
2019-07-18 10:56:40,507 : INFO : EPOCH 30 - PROGRESS: at 99.13% examples, 304800 words/s, in_qsize 31, out_qsize 0
2019-07-18 10:56:41,518 : INFO : EPOCH 30 - PROGRESS: at 99.17% examples, 304802 words/s, in_qsize 31, out_qsize 0
2019-07-18 10:56:42,541 : INFO : EPOCH 30 - PROGRESS: at 99.21% examples, 304806 words/s, in_qsize 31, out_qsize 0
2019-07-18 10:56:43,559 : INFO : EPOCH 30 - PROGRESS: at 99.25% examples, 304811 words/s, in_qsize 31, out_qsize 0
2019-07-18 10:56:44,567 : INFO : EPOCH 30 - PROGRESS: at 99.28% examples, 304814 words/s, in_qsize 31, out_qsize 0
2019-07-18 10:56:45,613 : INFO : EPOCH 30 - PROGRESS: at 99.32% examples, 304814 words/s, in_qsize 31, out_qsize 0
2019-07-18 10:56:46,631 : INFO : EPOCH 30 - PROGRESS: at 99.36% examples, 304816 words/s, in_qsize 31, out_qsize 0
2019-07-18 10:56:47,646 : INFO : EPOCH 30 - PROGRESS: at 99.40% examples, 304821

Wall time: 21h 32min 24s


In [68]:
## Sample of a tagged document
next(corpus_for_doc2vec.__iter__())

TaggedDocument(words=['battery', 'comprising', 'interior', 'battery', 'active', 'elements', 'battery', 'cell', 'casing', 'said', 'cell', 'casing', 'comprising', 'first', 'casing', 'element', 'first', 'contact', 'surface', 'second', 'casing', 'element', 'second', 'contact', 'surface', 'wherein', 'assembled', 'position', 'first', 'second', 'contact', 'surfaces', 'contact', 'first', 'second', 'casing', 'elements', 'encase', 'active', 'materials', 'battery', 'cell', 'interior', 'space', 'wherein', 'least', 'one', 'gas', 'tight', 'seal', 'layer', 'arranged', 'first', 'second', 'contact', 'surfaces', 'seal', 'interior', 'space', 'characterized', 'one', 'first', 'second', 'contact', 'surfaces', 'comprises', 'electrically', 'insulating', 'void', 'volume', 'layer', 'first', 'second', 'contact', 'surfaces', 'comprises', 'formable', 'material', 'layer', 'fills', 'voids', 'surface', 'void', 'volume', 'layer', 'hermetically', 'assembled', 'position', 'form', 'seal', 'layer'], tags=['8697278-17'])

In [7]:
next(iter(corpus_for_doc2vec))

TaggedDocument(words=['battery', 'comprising', 'interior', 'battery', 'active', 'elements', 'battery', 'cell', 'casing', 'said', 'cell', 'casing', 'comprising', 'first', 'casing', 'element', 'first', 'contact', 'surface', 'second', 'casing', 'element', 'second', 'contact', 'surface', 'wherein', 'assembled', 'position', 'first', 'second', 'contact', 'surfaces', 'contact', 'first', 'second', 'casing', 'elements', 'encase', 'active', 'materials', 'battery', 'cell', 'interior', 'space', 'wherein', 'least', 'one', 'gas', 'tight', 'seal', 'layer', 'arranged', 'first', 'second', 'contact', 'surfaces', 'seal', 'interior', 'space', 'characterized', 'one', 'first', 'second', 'contact', 'surfaces', 'comprises', 'electrically', 'insulating', 'void', 'volume', 'layer', 'first', 'second', 'contact', 'surfaces', 'comprises', 'formable', 'material', 'layer', 'fills', 'voids', 'surface', 'void', 'volume', 'layer', 'hermetically', 'assembled', 'position', 'form', 'seal', 'layer'], tags=['8697278-17'])

In [79]:
model.wv.vocab['government'].count

1894

2

In [8]:
#from gensim.test.utils import get_tmpfile
## MAIN MODEL ##
fname = os.getcwd()+"\\Doc2vec_Patent_Claims_FINAL_dm_30e"

## EXPERIMENTAL MODEL ##
#fname = os.getcwd()+"\\Doc2vec_Patent_Claims_FINAL_dm_30e_Lit_tagged"

#model_smple.save(fname)

model = Doc2Vec.load(fname)

2019-08-14 12:46:16,447 : INFO : loading Doc2Vec object from D:\Datasets\Doc2vec_Patent_Claims_FINAL_dm_30e
2019-08-14 12:46:30,013 : INFO : loading vocabulary recursively from D:\Datasets\Doc2vec_Patent_Claims_FINAL_dm_30e.vocabulary.* with mmap=None
2019-08-14 12:46:30,014 : INFO : loading trainables recursively from D:\Datasets\Doc2vec_Patent_Claims_FINAL_dm_30e.trainables.* with mmap=None
2019-08-14 12:46:30,015 : INFO : loading syn1neg from D:\Datasets\Doc2vec_Patent_Claims_FINAL_dm_30e.trainables.syn1neg.npy with mmap=None
2019-08-14 12:46:30,120 : INFO : loading wv recursively from D:\Datasets\Doc2vec_Patent_Claims_FINAL_dm_30e.wv.* with mmap=None
2019-08-14 12:46:30,121 : INFO : loading vectors from D:\Datasets\Doc2vec_Patent_Claims_FINAL_dm_30e.wv.vectors.npy with mmap=None
2019-08-14 12:46:30,252 : INFO : loading docvecs recursively from D:\Datasets\Doc2vec_Patent_Claims_FINAL_dm_30e.docvecs.* with mmap=None
2019-08-14 12:46:30,253 : INFO : loading vectors_docs from D:\Datase

In [26]:
### Test Code
lit = df.loc[df['litigation']==1,:]
non_lit = df.loc[df['litigation']==0,:]


In [29]:
### Test Code
model_smple.wv.similarity_matrix()

#most_similar_to_given('8697278-1',non_lit)

KeyError: "word '8697278-1' not in vocabulary"

In [9]:
### sample output
## takes in tagged document 

def model_infer_test(df,model):
    #grab a random claim from random_claim funciton
    tagged_claim = next(random_claim(df))
    #Infer a vector from that claim
    inferred_vector = model.infer_vector(tagged_claim.words)
    # this takes FOREVER with a long corpus cut the corpus in half to make it fast
    sims = model.docvecs.most_similar([inferred_vector], topn=len(model.docvecs)) 
    
    print(sims[:5])
    # Compare and print the most/median/least similar documents from the train corpus
    print('Test Document ({}): «{}»\n'.format(tagged_claim.tags, ' '.join(tagged_claim.words)))
    print(u'SIMILAR/DISSIMILAR DOCS PER MODEL %s:\n' % model)
    for label, index in [('MOST', 0),('Second', 1) ,('MEDIAN', len(sims)//2), ('LEAST', len(sims) - 1)]:
        
        print(label,index)
        #print(u'%s %s: «%s»\n' % (label, sims[index], ' '.join(df[sims[index][0]].words)))
        print(u'%s %s: «%s»\n' % (label, sims[index], df.loc[df['claim_no']==sims[index][0],['claim_txt']].values))

# This will let you get random tagged documents
def random_claim(df):
    doc_index =  np.random.randint(0,len(df))
    #row = [df.iloc[doc_index,:]['claim_txt'],df.iloc[doc_index,:]['claim_no']]
    yield TaggedDocument(words=simple_preprocess(df.iloc[doc_index,:]['claim_txt']), 
                             tags=df.iloc[doc_index,:]['claim_no'])


In [57]:
model_infer_test(df,model_smple)

[('6208475-7', 0.9243185520172119), ('6208475-3', 0.883671224117279), ('6680491-1', 0.6106572151184082), ('8913211-14', 0.5911911725997925), ('8913211-1', 0.5858227610588074)]
Test Document (6208475-7): «optical member inspection apparatus obtaining image data used inspections applying illumination light optical member one side thereof photographing optical member side comprising holder comprising frame shaped base portion plurality spaced optical member holding portions provided base portion enclose space supporting optical member formed base portion said optical member holding portions receiving face outer margin optical member mounted restriction wall restrict movement optical member mounted receiving face contacting outer margin optical member said receiving face contacting outer margin face optical member light passes operation optical member said restricting wall located said moving face»

SIMILAR/DISSIMILAR DOCS PER MODEL Doc2Vec(dm/m,d100,n5,w5,mc2,s0.001,t16):

MOST 0
MOST ('6

In [20]:
def search(query,model):
    inferred_vector = model.infer_vector(simple_preprocess(query))
    sims = model.docvecs.most_similar([inferred_vector], topn=len(model.docvecs))
    return query,sims[:10]


In [24]:
query = "A method of determining isometric relationships in an articulated mammalian joint, comprising:(a) identifying a reference point on an image of one bone in said joint and an isometric point on an image of a second bone in said joint which appears isometric to said reference point in at least two images of the joint, said two images respectively showing said joint in flexed and extended positions" 
search(query,model)


('A method of determining isometric relationships in an articulated mammalian joint, comprising:(a) identifying a reference point on an image of one bone in said joint and an isometric point on an image of a second bone in said joint which appears isometric to said reference point in at least two images of the joint, said two images respectively showing said joint in flexed and extended positions',
 [('8523949-1', 0.5725446939468384),
  ('6493574-15', 0.5441705584526062),
  ('6080431-16', 0.5297740697860718),
  ('7905924-1', 0.5226974487304688),
  ('6214014-6', 0.5177952647209167),
  ('6640127-43', 0.5174787640571594),
  ('RE37249-5', 0.5049606561660767),
  ('8010177-13', 0.5034835934638977),
  ('7925331-16', 0.5029727220535278),
  ('6214014-1', 0.5025979280471802)])

In [32]:
query = df.loc[df['claim_no']=="7905924-1"]['claim_txt'].values[0]
search(query,model)

('method providing stabilizing extracapsular surgical repair articulating joint two bones mammalian subject, comprising: (a) obtaining pair images, first image said pair showing said articulating joint fully flexed position second image said pair showing said articulating joint fully extended position; (b) said images identifying pair points provide extracapsular tension-carrying structure interconnecting said two bones, said pair points reference point first one said two bones isometric point second one said two bones, said reference isometric points located said joint separated separation distance equal said first second images; (c) providing measuring locating device having: (i) body; (ii) pair locating portions associated said body, least one said locating portions adjustably located respect said body; (iii) scale capable providing indication separation distance said locating portions; (d) locating said reference point said first one said bones said articulating joint said subject;

In [33]:
query = "A method and device for finding isometric points in the joints of mammals for use in surgical repair of a joint. Isometric points are first identified in radiographic or other two dimensional images and then located in the actual joint. A method for repairing a cruciate ligament-deficient canine stifle employing the method and device for finding isometric points is described. A method and apparatus for locating the axis of rotation of a joint is also described."
search(query,model)

('A method and device for finding isometric points in the joints of mammals for use in surgical repair of a joint. Isometric points are first identified in radiographic or other two dimensional images and then located in the actual joint. A method for repairing a cruciate ligament-deficient canine stifle employing the method and device for finding isometric points is described. A method and apparatus for locating the axis of rotation of a joint is also described.',
 [('6060501-11', 0.5635033845901489),
  ('8748644-1', 0.5616990327835083),
  ('6255261-2', 0.5598280429840088),
  ('6294551-7', 0.5532804727554321),
  ('7138397-9', 0.5493271350860596),
  ('8147833-1', 0.5453063249588013),
  ('7683179-11', 0.5424196124076843),
  ('RE30413-1', 0.5419983267784119),
  ('6121257-1', 0.5385806560516357),
  ('6053869-1', 0.5349327325820923)])

In [27]:
df.loc[df['claim_no']=='6857067-107','claim_txt'].values



array(['computer code executable electronic device prevent unauthorized access electronic data stored electronic device, computer code comprising: code storing license data portable licensing medium configured communicate electronic device; code determining whether allow access electronic data based license data; code verifying license data stored licensing medium communicating registration authority verification data; code providing updated license data received registration authority licensing medium.'],
      dtype=object)

In [22]:
#input df , doc2vec model, patent-claim#, topn sim

#output = top similar patent claims
def top_claim_sim(df,model,index,n=10):
    
    tagged_claim = TaggedDocument(words=simple_preprocess(df.loc[df['claim_no']==index,'claim_txt'].values), 
                             tags=index)
    claim_vector = model.infer_vector(tagged_claim.words)
    return model.docvecs.most_similar([claim_vector], topn=n)

In [23]:
top_claim_sim(df,model,'7905924-1')

[('7649545-11', 0.4929351806640625),
 ('7649545-17', 0.48775380849838257),
 ('8345255-20', 0.48668646812438965),
 ('8526322-7', 0.4812292158603668),
 ('7580409-55', 0.48066794872283936),
 ('7649545-12', 0.4803555905818939),
 ('7990992-18', 0.48008671402931213),
 ('6570716-2', 0.4781513512134552),
 ('6779272-13', 0.47323498129844666),
 ('7373173-28', 0.4729830324649811)]

In [22]:
# This will let you get random tagged documents

def random_claim(df):
    doc_index =  np.random.randint(0,len(df))
    #row = [df.iloc[doc_index,:]['claim_txt'],df.iloc[doc_index,:]['claim_no']]
    yield TaggedDocument(words=simple_preprocess(df.iloc[doc_index,:]['claim_txt']), 
                             tags=df.iloc[doc_index,:]['claim_no']).words

In [24]:
next(random_claim(df))

['method',
 'optimizing',
 'data',
 'path',
 'along',
 'data',
 'packets',
 'exchanged',
 'first',
 'communication',
 'node',
 'second',
 'communication',
 'node',
 'communications',
 'system',
 'wherein',
 'least',
 'first',
 'communication',
 'node',
 'located',
 'foreign',
 'network',
 'method',
 'comprising',
 'steps',
 'of',
 'transmitting',
 'first',
 'communication',
 'node',
 'local',
 'connection',
 'request',
 'management',
 'entity',
 'first',
 'communication',
 'node',
 'foreign',
 'network',
 'local',
 'connection',
 'request',
 'comprising',
 'identity',
 'information',
 'second',
 'communication',
 'node',
 'determining',
 'management',
 'entity',
 'foreign',
 'network',
 'response',
 'received',
 'local',
 'connection',
 'request',
 'local',
 'data',
 'gateway',
 'foreign',
 'network',
 'based',
 'identity',
 'information',
 'second',
 'communication',
 'node',
 'wherein',
 'local',
 'data',
 'gateway',
 'determined',
 'gateway',
 'second',
 'communication',
 'node',
 '

In [58]:
%%time
#doc_index =  np.random.randint(0,len(df))
doc_index = len(df)-1
### This is faster than
row = [df.iloc[doc_index,:]['claim_txt'],df.iloc[doc_index,:]['claim_no']]
### This for some reason ?! 0 nano seconds vs 1ms 
#row = df.loc[doc_index,['claim_txt','claim_no']].values


Wall time: 0 ns


In [7]:
### attempt to vectorize the function calling along the dataframe chunks.



def get_tokens(col):
    return gensim.utils.simple_preprocess(col)

def calc_vectors(tokens,model):
    return model.infer_vector((tokens),steps=20)


In [8]:
%%time
class get_vectors(object):
    def __init__(self, source_df, text_col, tag_col,model):
        self.source_df = source_df
        self.text_col = text_col
        self.tag_col = tag_col
        self.model = model
    #### Works but does not have a way to merge with source DF  
    def __iter__(self):
        # overly verbose function give me the claim-id and the vector of the tagged document from the claim
        for i, row in self.source_df.iterrows():
            yield self.model.infer_vector(TaggedDocument(words=simple_preprocess(row[self.text_col]), 
                                 tags=[row[self.tag_col]]).words,steps=20), row[self.tag_col]
            
            
df_vect_test = get_vectors(df,'claim_txt','claim_no',model)
vecs , tags = list(map(list,zip(*df_vect_test)))
df_vectors = pd.DataFrame(data=vecs,index = tags)
df_vectors.index.name = 'claim_no'

Wall time: 6h 35min 34s


claim_no                                          claim_txt  ICL  ICC  \
0  8697278-17  battery comprising interior battery active ele...  106    2   
1   8697278-1  battery cell casing comprising first casing el...   97    2   
2  7385756-81  catadioptric projection objective imaging patt...  108   33   
3  7385756-94  catadioptric projection objective imaging patt...  116   33   
4  7385756-79  catadioptric projection objective imaging patt...  103   33   

   litigation  
0           0  
1           0  
2           0  
3           0  
4           0

In [10]:
def text_me(i,filename,end,start):
    fake = 'done training'
    message = client.messages.create(
                                from_='whatsapp:+14155238886',
                                #body=f'Built the vocab boss it took {(end-start)/60}  minutes',
                                body=f'Your {filename} code is {fake, (end-start)/60}',
                                to='whatsapp:+19715704109'
                              )

claim_no                                          claim_txt  ICL  ICC  \
0  8697278-17  battery comprising interior battery active ele...  106    2   
1   8697278-1  battery cell casing comprising first casing el...   97    2   
2  7385756-81  catadioptric projection objective imaging patt...  108   33   
3  7385756-94  catadioptric projection objective imaging patt...  116   33   
4  7385756-79  catadioptric projection objective imaging patt...  103   33   

   litigation  
0           0  
1           0  
2           0  
3           0  
4           0

In [9]:
### Text me when this shit is done
from twilio.rest import Client

# client credentials are read from TWILIO_ACCOUNT_SID and AUTH_TOKEN
client = Client("AC50ac8d9e423ca2324fd0aaa5dc91e4d1", "76be2cf406ea4cbb4577985c95a8e4d2")

# this is the Twilio sandbox testing number
from_whatsapp_number='whatsapp:+14155238886'
# replace this number with your own WhatsApp Messaging number
to_whatsapp_number='whatsapp:+19715704109'

In [13]:
%%time
df.index=df['claim_no']
df.drop(['claim_no'],axis=1,inplace=True)
### Merge vectors with data.

df_final = pd.merge(df,df_vectors,how='inner',on='claim_no')
#df_vectors.head()

df_final.info()

<class 'pandas.core.frame.DataFrame'>
Index: 8216031 entries, 8697278-17 to 8794966-1
Columns: 104 entries, claim_txt to 99
dtypes: float64(100), int64(3), object(1)
memory usage: 6.4+ GB
Wall time: 47.3 s


In [17]:
df_final.to_csv('claims_vectors_litigation.csv',index=True)

In [ ]:
df_final.drop('claim_txt',axis=1,inplace=True)

In [18]:
del df, df_vectors, vecs , tags

In [236]:
vecs , tags = list(map(list,zip(*df_vect_test)[:10]))
blah = pd.DataFrame(data=vecs,index = tags)
blah

KeyboardInterrupt: 

In [60]:
%%time
%time tokens = df['claim_txt'].apply((lambda row : get_tokens(row)))
%time vectors = tokens.apply((lambda row : calc_vectors(row,model_smple)))
del tokens
%time df_vectors = vectors.apply(lambda x : pd.Series(x))
del vectors
#%time df_vectors.to_csv('test_vectors_to_merge.csv')

### I should use yields and generators for this but i'm in a rush

Wall time: 25min 48s


NameError: name 'model' is not defined

NameError: name 'vectors' is not defined

NameError: name 'vectors' is not defined

In [155]:
#df_vectors = df['claim_txt'][:10].apply((lambda row : get_tokens(row))).apply((lambda row : calc_vectors(row,model_smple))).apply(lambda x : pd.Series(x))

df_vect_test = get_vectors(df[:10],'claim_txt','claim_no',model_smple)

In [120]:
#df['claim_txt'][:10].apply((lambda row : get_tokens(row))).apply(lambda row :calc_vectors(row,model_smple)).apply(lambda x : pd.Series(x))

0         1         2         3         4         5         6   \
0 -0.107780  0.601903 -0.280853  1.677937  0.994736  0.235104  1.099690   
1  0.082769  0.234462 -0.274393  1.379142  1.121734 -0.188325  1.042254   
2  1.320151  0.690203 -0.067970 -1.125389 -0.337494  0.058603 -0.826842   
3  0.914507  0.658234 -0.768697 -1.065891 -0.476972 -0.237683 -0.692387   
4  1.352883  0.808135 -0.072673 -0.470193 -0.485823  0.561617 -1.215139   
5  1.408415  0.846687 -0.805871 -0.876863 -0.466241 -0.739602  0.132335   
6  1.318740  0.698713 -0.385702 -1.100168 -0.442286 -0.216008 -0.936316   
7  1.858155  0.607933 -1.038954 -0.587242 -0.360321  0.558012 -0.145877   
8  1.149071  0.312484 -0.190671 -0.931803 -0.600381  0.152480 -0.773522   
9  1.257515  0.557460 -0.620070 -1.034003 -0.266954 -0.278317 -0.825467   

         7         8         9     ...           90        91        92  \
0  0.570822 -0.049077 -0.091883    ...    -1.192746 -0.437771  0.379722   
1  0.574875  0.176861 -0.112893    ...    -1.288304 -0.174551  0.651207   
2 -0.530852 -1.930141  0.372839    ...     0.378466  0.830113  0.525041   
3 -0.876860 -1.983994  0.167530    ...     0.792587  0.467129  1.026224   
4 -0.712734 -1.916998 -0.205722    ...    -0.096859  0.771595  1.237172   
5 -0.796044 -1.833705  0.908808    ...     0.267910  0.471827  0.706786   
6 -0.799015 -1.737944  0.412731    ...     0.525124  0.721694  0.633345   
7 -0.747977 -1.872106  0.479062    ...    -0.539310  0.159923  0.916942   
8 -0.670947 -1.704858  0.126621    ...     0.324091  0.728776  0.759854   
9 -0.522083 -1.756007  0.279793    ...     0.571532  0.764547  0.822939   

         93        94        95        96        97        98        99  
0 -0.885952 -0.058186  0.336634  0.038800 -0.986657 -0.521620 -2.073683  
1 -1.192964  0.173659  0.118450  0.502758 -0.951412 -0.497529 -1.772767  
2 -1.007813 -0.331908 -0.241523 -2.430176  0.295582  0.933696  0.768533  
3 -0.892889 -0.496014 -0.411153 -2.445151  0.193088  0.689275  0.711549  
4  0.232351 -0.665515 -0.266631 -2.514383  1.209349  0.072355  0.404568  
5 -0.513137 -0.723284  0.017169 -2.018531  0.916339  0.592488  0.741021  
6 -0.538245 -0.192534 -0.212918 -2.264540  0.364803  0.543640  0.405380  
7 -0.485154 -0.149518 -0.906893 -2.459996  1.030616  0.057868  0.668389  
8 -0.864537 -0.206817 -0.561864 -2.657154  0.163633  0.713839  0.895962  
9 -0.495428 -0.351081 -0.188938 -2.575629  0.119716  0.702917  0.455640  

[10 rows x 100 columns]

In [39]:
df_final.head()

ICL  ICC  litigation         0         1         2         3  \
claim_no                                                                   
8697278-17  106    2           0 -0.021915  0.124170 -0.467477  1.725972   
8697278-1    97    2           0 -0.271349  0.260269 -0.315466  1.746054   
7385756-81  108   33           0  1.429105  0.936555 -0.296551 -1.073354   
7385756-94  116   33           0  1.027478  0.484034 -0.535233 -1.124252   
7385756-79  103   33           0  1.396978  0.419591 -0.072397 -0.642861   

                   4         5         6    ...           90        91  \
claim_no                                    ...                          
8697278-17  1.353391 -0.197958  1.234415    ...    -1.201108 -0.272672   
8697278-1   0.874254 -0.225060  0.971804    ...    -1.190130 -0.417508   
7385756-81 -0.421059 -0.114407 -0.881726    ...     0.885844  0.934247   
7385756-94 -0.382812 -0.101879 -0.348340    ...     0.772912  0.951951   
7385756-79 -0.482944  0.496666 -1.178749    ...     0.074441  1.187986   

                  92        93        94        95        96        97  \
claim_no                                                                 
8697278-17  0.649778 -1.023098  0.146432  0.122571  0.215042 -1.076661   
8697278-1   0.587534 -1.157797  0.314950  0.189521  0.474607 -1.119020   
7385756-81  0.678008 -0.752642 -0.121980 -0.623260 -2.384536  0.471751   
7385756-94  0.901475 -0.721144 -0.304449 -0.278908 -2.655865  0.323664   
7385756-79  0.909484  0.278953 -0.483475 -0.028059 -2.268470  0.986993   

                  98        99  
claim_no                        
8697278-17 -0.508896 -1.690101  
8697278-1  -0.376173 -1.699343  
7385756-81  0.874406  1.251178  
7385756-94  0.943390  0.687369  
7385756-79  0.039141  0.374451  

[5 rows x 103 columns]